In [1]:
import nltk 
nltk.download()



showing info https://raw.githubusercontent.com/nltk/nltk_data/gh-pages/index.xml


True

In [2]:
pip install ir_datasets


Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [3]:
import ir_datasets


In [4]:
pip install flask

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [5]:
pip install datefinder

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [6]:
pip install textblob

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [7]:
pip install flask-cors


Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [8]:
import string
from nltk import pos_tag
import ir_datasets
from collections import defaultdict
import re
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.stem import PorterStemmer, WordNetLemmatizer
import sys
import os
import pandas as pd
import numpy as np
import matplotlib as plt
import nltk.stem as stemmer
from nltk.corpus import stopwords,words
from nltk.metrics.distance import jaccard_distance
from nltk.util import ngrams
from collections import defaultdict
import re
lemmatizer = WordNetLemmatizer()
from datetime import datetime

import nltk.tokenize as nt

In [9]:
import pandas as pd

In [10]:
ddf=pd.read_csv(r'C:\Users\omer\.ir_datasets\cord19\2020-06-19\metadata.csv')

C:\Users\omer\AppData\Local\Temp\ipykernel_2868\3140937985.py:1: DtypeWarning: Columns (5,13,14,16) have mixed types. Specify dtype option on import or set low_memory=False.
  ddf=pd.read_csv(r'C:\Users\omer\.ir_datasets\cord19\2020-06-19\metadata.csv')


In [11]:
ddf.head()

cord_uid                                       sha source_x  \
0  ug7v899j  d1aafb70c066a2068b02786f8929fd9c900897fb      PMC   
1  02tnwd4m  6b0567729c2143a66d737eb0a2f63f2dce2e5a7d      PMC   
2  ejv2xln0  06ced00a5fc04215949aa72528f2eeaae1d58927      PMC   
3  2b73a28n  348055649b6b8cf2b9a376498df9bf41f7123605      PMC   
4  9785vg6d  5f48792a5fa08bed9f56016f4981ae2ca6031b32      PMC   

                                               title                    doi  \
0  Clinical features of culture-proven Mycoplasma...  10.1186/1471-2334-1-6   
1  Nitric oxide: a pro-inflammatory mediator in l...           10.1186/rr14   
2    Surfactant protein-D and pulmonary host defense           10.1186/rr19   
3               Role of endothelin-1 in lung disease           10.1186/rr44   
4  Gene expression in epithelial cells in respons...           10.1186/rr61   

      pmcid   pubmed_id license  \
0  PMC35282  11472636.0   no-cc   
1  PMC59543  11667967.0   no-cc   
2  PMC59549  11667972.0   no-cc   
3  PMC59574  11686871.0   no-cc   
4  PMC59580  11686888.0   no-cc   

                                            abstract publish_time  \
0  OBJECTIVE: This retrospective chart review des...   2001-07-04   
1  Inflammatory diseases of the respiratory tract...   2000-08-15   
2  Surfactant protein-D (SP-D) participates in th...   2000-08-25   
3  Endothelin-1 (ET-1) is a 21 amino acid peptide...   2001-02-22   
4  Respiratory syncytial virus (RSV) and pneumoni...   2001-05-11   

                                             authors         journal  mag_id  \
0                Madani, Tariq A; Al-Ghamdi, Aisha A  BMC Infect Dis     NaN   
1  Vliet, Albert van der; Eiserich, Jason P; Cros...      Respir Res     NaN   
2                                    Crouch, Erika C      Respir Res     NaN   
3  Fagan, Karen A; McMurtry, Ivan F; Rodman, David M      Respir Res     NaN   
4  Domachowske, Joseph B; Bonville, Cynthia A; Ro...      Respir Res     NaN   

  who_covidence_id arxiv_id  \
0              NaN      NaN   
1              NaN      NaN   
2              NaN      NaN   
3              NaN      NaN   
4              NaN      NaN   

                                      pdf_json_files  \
0  document_parses/pdf_json/d1aafb70c066a2068b027...   
1  document_parses/pdf_json/6b0567729c2143a66d737...   
2  document_parses/pdf_json/06ced00a5fc04215949aa...   
3  document_parses/pdf_json/348055649b6b8cf2b9a37...   
4  document_parses/pdf_json/5f48792a5fa08bed9f560...   

                               pmc_json_files  \
0  document_parses/pmc_json/PMC35282.xml.json   
1  document_parses/pmc_json/PMC59543.xml.json   
2  document_parses/pmc_json/PMC59549.xml.json   
3  document_parses/pmc_json/PMC59574.xml.json   
4  document_parses/pmc_json/PMC59580.xml.json   

                                                 url  s2_id  
0  https://www.ncbi.nlm.nih.gov/pmc/articles/PMC3...    NaN  
1  https://www.ncbi.nlm.nih.gov/pmc/articles/PMC5...    NaN  
2  https://www.ncbi.nlm.nih.gov/pmc/articles/PMC5...    NaN  
3  https://www.ncbi.nlm.nih.gov/pmc/articles/PMC5...    NaN  
4  https://www.ncbi.nlm.nih.gov/pmc/articles/PMC5...    NaN

In [13]:
# Remove null values from the 'title' column
ddf = ddf.dropna(subset=['cord_uid','title','abstract'])

In [14]:
import re

def replace_percont_text(text):
    percont_text = text.replace('%', ' percent') # Remove punctuations
    return percont_text


Expand Country Abbreviations

In [15]:
country_abbreviations = {
    'USA': 'United States of America',
    'UK': 'United Kingdom',
    'UAE': 'United Arab Emirates',
    'ROK': 'Republic of Korea',
    'PRC': "People's Republic of China",
    'ROC': 'Republic of China',
    'DPRK': "Democratic People's Republic of Korea",
    'RSA': 'Republic of South Africa',
    'KSA':'Kingdom of Saudi Arabia'
}

def expand_country_abbreviations(text):
    # Check if the input text is a string
    if isinstance(text, str):
        for abbreviation, expanded_form in country_abbreviations.items():
            text = text.replace(abbreviation, expanded_form)
    return text




In [16]:
date_abbreviations = {
    'Jan': 'January',
    'Feb': 'February',
    'Mar': 'March',
    'Apr': 'April',
    'May': 'May',
    'Jun': 'June',
    'Jul': 'July',
    'Aug': 'August',
    'Sep': 'September',
    'Oct': 'October',
    'Nov': 'November',
    'Dec': 'December'
}

def expand_date_abbreviations(text):
    # Check if the input text is a string
    if isinstance(text, str):
        for abbreviation, expanded_form in date_abbreviations.items():
            text = text.replace(abbreviation, expanded_form)
    return text



Remove punctuations

In [17]:
import re

def clean_text(text):
    text = re.sub(r'[^\w\s]', ' ', text) # Remove punctuations
    return text




lower text

In [18]:
def lower_text(text):
    text = text.lower() # Convert to lowercase
    return text




Lemmtization 

In [19]:
import nltk
from nltk.stem import WordNetLemmatizer

def lemmatize_text(text):
    lemmatizer = WordNetLemmatizer()
    return ' '.join([lemmatizer.lemmatize(word) for word in nltk.word_tokenize(text)])



Stemmer

In [20]:
import nltk
from nltk.stem import PorterStemmer
stemmer = PorterStemmer()
def stem_text(text):
    tokens = nltk.word_tokenize(text)
    stems = [stemmer.stem(token) for token in tokens]
    return ' '.join(stems)


Tokenize and remove stop words

In [21]:
import nltk
import nltk
from nltk.corpus import stopwords
import json

def tokenize_and_remove_stop_words(text):
    # Tokenize the text into words
    words = nltk.word_tokenize(text)
    
    # Remove stop words
    stop_words = set(stopwords.words('english'))
    filtered_words = [word.lower() for word in words if word.lower() not in stop_words and word.isalpha()]
    
    return filtered_words

# Create a dictionary to store the tokenized titles/abstracts
tokenized_dict = {}

# Loop through each row of the DataFrame
for i, row in ddf.iterrows():
    # Tokenize the title and abstract and remove stop words
    title_tokens = tokenize_and_remove_stop_words(row['title'])
    abstract_tokens = tokenize_and_remove_stop_words(row['abstract'])
    
    # Add the tokenized title and abstract to the dictionary
    tokenized_dict[str(row['cord_uid'])] = title_tokens + abstract_tokens

    
# Print the tokenized dictionary
# Print the first 10 key-value pairs in the tokenized dictionary
for i, (key, value) in enumerate(tokenized_dict.items()):
    if i < 1:
        print(f"{key}: {value}")
    else:
        break

ug7v899j: ['clinical', 'features', 'mycoplasma', 'pneumoniae', 'infections', 'king', 'abdulaziz', 'university', 'hospital', 'jeddah', 'saudi', 'arabia', 'objective', 'retrospective', 'chart', 'review', 'describes', 'epidemiology', 'clinical', 'features', 'patients', 'mycoplasma', 'pneumoniae', 'infections', 'king', 'abdulaziz', 'university', 'hospital', 'jeddah', 'saudi', 'arabia', 'methods', 'patients', 'positive', 'pneumoniae', 'cultures', 'respiratory', 'specimens', 'january', 'december', 'identified', 'microbiology', 'records', 'charts', 'patients', 'reviewed', 'results', 'patients', 'identified', 'required', 'admission', 'infections', 'infection', 'affected', 'age', 'groups', 'common', 'infants', 'children', 'occurred', 'common', 'fall', 'spring', 'patients', 'comorbidities', 'isolates', 'associated', 'pneumonia', 'upper', 'respiratory', 'tract', 'infections', 'bronchiolitis', 'cough', 'fever', 'malaise', 'common', 'symptoms', 'crepitations', 'wheezes', 'common', 'signs', 'patient

In [22]:
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/tokenized_dict.json', 'w') as f:
        json.dump(dict(tokenized_dict), f)
    

In [22]:
import json

# Load the tokenized_dict from file
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/tokenized_dict.json', 'r') as f:
    tokenized_dict_f = json.load(f)

# Example usage
print(len(tokenized_dict_f)) # Print the number of documents in the corpus

116374


Inverted Index

In [23]:
import nltk
from collections import defaultdict
import json

def create_inverted_index(tokenized_dict):
    inverted_index = defaultdict(list)
    for x, doc_content in tokenized_dict.items():
        # Combine the "title" and "abstract" fields
        text = " ".join(doc_content)
        
        # Tokenize the text and apply any desired text preprocessing steps
        terms = [term.lower() for term in nltk.word_tokenize(text) if term.isalnum()]

        # Add the doc_id to the list associated with each term in the inverted index
        for term in terms:
            inverted_index[term].append(x)
    
    return dict(inverted_index)

# Assuming that the tokenized_dict is a dictionary with document ids as keys and tokenized titles/abstracts as values
inverted_index = create_inverted_index(tokenized_dict)
# Create a file object in write mode

    

for i, (key, value) in enumerate(inverted_index.items()):
    if i < 10:
        print(f"{key}: {value}")
    else:
        break

clinical: ['ug7v899j', 'ug7v899j', '5yhe786e', '8zchiykl', 'jg13scgo', 't35n7bk9', '4cvy9u28', 'tw6wusxe', '58czem0j', 'utglk4af', 'w5fxen70', 'p5jtwb3l', 'nhb4o6ty', '5fl0rk90', 'kuf3ssdb', 'hf3nytb2', '4y8ghcpq', '4y8ghcpq', '63bos83o', 'lz37rh82', 'kfwbqp4p', 'mzn448zk', 'd37u3qbd', 'd37u3qbd', 'd37u3qbd', 'd37u3qbd', 'd37u3qbd', 'd37u3qbd', 'd37u3qbd', 'fae3sczm', 'fae3sczm', 'fae3sczm', 'fae3sczm', '33mqfj2t', '33mqfj2t', '543aq9dx', '543aq9dx', '8rrkf78o', 'ze511t38', 'ze511t38', 'rnvh9ut8', 'rnvh9ut8', 'ajafw966', 'ajafw966', 'ajafw966', 'dg3pfydf', 'oz823tw4', 'oz823tw4', 'nv228vte', 'nv228vte', '5j496cx0', '5j496cx0', 'osioowtp', 'osioowtp', 'ciuhyhb8', '87mjdccj', 'q75spbgv', 'q75spbgv', 'q75spbgv', 'q75spbgv', '10j9cp9c', '533xlisc', '533xlisc', 'jy7j8sh0', 'jy7j8sh0', 'jy7j8sh0', 't579ysgl', 'vueo83vk', 'vueo83vk', 'vueo83vk', 'd0eur1hq', 'd0eur1hq', 'd0eur1hq', 'd0eur1hq', 'ujgcsx3o', '3qxun84i', '3qxun84i', '3qxun84i', 'kxtdv6q9', 'duwfxeyt', 'ejha0oh6', 'idffrnac', 'idff

In [24]:
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/inverted_index.json', 'w') as f:
        json.dump(dict(inverted_index), f)
    

In [25]:
import json

# Load the tokenized_dict from file
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/inverted_index.json', 'r') as f:
    inverted_index_f = json.load(f)

# Example usage
print(len(inverted_index_f)) # Print the number of documents in the corpus

151872


Calculate tf_idf 

In [26]:
import math
from collections import defaultdict
def calculate_tf(document):
    my_string = " ".join(document)
    print (my_string)
    tf = {}
    terms = my_string.split()
    term_count = len(terms)
    for term in terms:
        tf[term] = terms.count(term)/term_count
    return tf


In [27]:
def convert_corpus():
    i=1
    temp={}
    for key,value in tokenized_dict_f.items():
        my_string = " ".join(value)
        temp[key]=my_string
       
    return temp

temp=convert_corpus();




In [28]:
first_key = next(iter(temp))
first_value = temp[first_key]
print(first_key)
print(first_value)

ug7v899j
clinical features mycoplasma pneumoniae infections king abdulaziz university hospital jeddah saudi arabia objective retrospective chart review describes epidemiology clinical features patients mycoplasma pneumoniae infections king abdulaziz university hospital jeddah saudi arabia methods patients positive pneumoniae cultures respiratory specimens january december identified microbiology records charts patients reviewed results patients identified required admission infections infection affected age groups common infants children occurred common fall spring patients comorbidities isolates associated pneumonia upper respiratory tract infections bronchiolitis cough fever malaise common symptoms crepitations wheezes common signs patients pneumonia crepitations bronchial breathing immunocompromised patients likely patients present pneumonia versus p patients pneumonia uneventful recovery recovered following complications died pneumoniae infection died due underlying comorbidities p

In [29]:
import json
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/corpus.json', 'w') as f:
        json.dump(dict(temp), f)
    

In [64]:
import json

# Load the tokenized_dict from file
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/corpus.json', 'r') as f:
    temp = json.load(f)

# Example usage
print(len(temp)) # Print the number of documents in the corpus

116374


In [65]:
import json

# Load the tokenized_dict from file
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/corpus.json', 'r') as f:
    temp = json.load(f)

# Extract keys and values
keys = list(temp.keys())
values = list(temp.values())

# Save keys to a JSON file named 'keys.json'
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/keys.json', 'w') as key_file:
    json.dump(keys, key_file, indent=4)

# Save values to a JSON file named 'documents.json'
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/documents.json', 'w') as value_file:
    json.dump(values, value_file, indent=4)

# Example usage
print(len(temp))  # Print the number of documents in the corpus


116374


In [67]:
import json

# Load the tokenized_dict from file
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/corpus.json', 'r') as f:
    temp = json.load(f)

# Extract keys and values
keys = list(temp.keys())
values = list(temp.values())

# Save keys to a JSON file named 'keys.json'
keys_path = 'C:/Users/omer/.ir_datasets/cord19/2020-06-19/keys.json'
with open(keys_path, 'w') as key_file:
    json.dump(keys, key_file, indent=4)

# Save values to a JSON file named 'documents.json'
values_path = 'C:/Users/omer/.ir_datasets/cord19/2020-06-19/documents.json'
with open(values_path, 'w') as value_file:
    json.dump(values, value_file, indent=4)

# Read keys from the 'keys.json' file
with open(keys_path, 'r') as key_file:
    saved_keys = json.load(key_file)

# Read values from the 'documents.json' file
with open(values_path, 'r') as value_file:
    saved_values = json.load(value_file)

# Print the first 10 elements from the 'keys.json' file
print("First 10 keys:")
for key in saved_keys[:10]:
    print(key)

# Print the first 10 elements from the 'documents.json' file
print("\nFirst 10 documents:")
for doc in saved_values[:10]:
    print(doc)


First 10 keys:
ug7v899j
02tnwd4m
ejv2xln0
2b73a28n
9785vg6d
zjufx4fo
5yhe786e
8zchiykl
8qnrcgnk
jg13scgo

First 10 documents:
clinical features mycoplasma pneumoniae infections king abdulaziz university hospital jeddah saudi arabia objective retrospective chart review describes epidemiology clinical features patients mycoplasma pneumoniae infections king abdulaziz university hospital jeddah saudi arabia methods patients positive pneumoniae cultures respiratory specimens january december identified microbiology records charts patients reviewed results patients identified required admission infections infection affected age groups common infants children occurred common fall spring patients comorbidities isolates associated pneumonia upper respiratory tract infections bronchiolitis cough fever malaise common symptoms crepitations wheezes common signs patients pneumonia crepitations bronchial breathing immunocompromised patients likely patients present pneumonia versus p patients pneumoni

In [31]:
i=0
for key,value in temp.items():
    if(i<5):
        print(f"{key}: {value}")
        i+=1

ug7v899j: clinical features mycoplasma pneumoniae infections king abdulaziz university hospital jeddah saudi arabia objective retrospective chart review describes epidemiology clinical features patients mycoplasma pneumoniae infections king abdulaziz university hospital jeddah saudi arabia methods patients positive pneumoniae cultures respiratory specimens january december identified microbiology records charts patients reviewed results patients identified required admission infections infection affected age groups common infants children occurred common fall spring patients comorbidities isolates associated pneumonia upper respiratory tract infections bronchiolitis cough fever malaise common symptoms crepitations wheezes common signs patients pneumonia crepitations bronchial breathing immunocompromised patients likely patients present pneumonia versus p patients pneumonia uneventful recovery recovered following complications died pneumoniae infection died due underlying comorbidities 

In [32]:


# write 
def calculate_idf(corpus):
    
    idf = {}
    n_docs = len(corpus)
    inverted_index = inverted_index_f
    for term, doc_ids in inverted_index.items():
        idf[term] = math.log(n_docs/len(doc_ids))
    return idf



In [33]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer

documents = list(map(str, temp.values()))  # Convert values of temp to strings using map

# Create a TfidfVectorizer object
vectorizer = TfidfVectorizer()

# Fit the vectorizer to the documents
tfidf_matrix = vectorizer.fit_transform(documents)




In [34]:
import os
from scipy.sparse import save_npz

# Specify the file path for storing the TF-IDF matrix
file_path = 'C:/Users/omer/.ir_datasets/cord19/2020-06-19/files/tfidf_matrix_file.npz'

# Create the directory if it doesn't exist
directory = os.path.dirname(file_path)
if not os.path.exists(directory):
    os.makedirs(directory)

# Save the TF-IDF matrix to the specified file path
save_npz(file_path, tfidf_matrix)

In [35]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from scipy.sparse import save_npz

documents = list(map(str, temp.values()))  # Convert values of temp to strings using map

# Specify the file path for storing the TF-IDF matrix
file_path = 'C:/Users/omer/.ir_datasets/cord19/2020-06-19/files/tfidf_matrix_file.npz'

# Save the TF-IDF matrix to the specified file path
save_npz(file_path, tfidf_matrix)


In [79]:
import pandas as pd
from scipy.sparse import load_npz

# Specify the file path where the TF-IDF matrix is stored
file_path = 'C:/Users/omer/.ir_datasets/cord19/2020-06-19/files/tfidf_matrix_file.npz'

# Load the TF-IDF matrix from the specified file path
tfidf_matrix = load_npz(file_path)



In [37]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from scipy.sparse import save_npz

documents = list(map(str, temp.values()))  # Convert values of temp to strings using map

# Create a TfidfVectorizer object
vectorizer = TfidfVectorizer()

# Fit the vectorizer to the documents
tfidf_matrix = vectorizer.fit_transform(documents)

# Specify the file path for storing the TF-IDF matrix
file_path = 'C:/Users/omer/.ir_datasets/beir/webis-touche2020/webis-touche2020/tfidf_matrix.npz'

# Save the TF-IDF matrix to the specified file path
save_npz(file_path, tfidf_matrix)


In [38]:
keys=list(map(str, temp.keys()))
i=0
# Print the map
for key in keys:
    if(i<5):
        print(key)
        i+=1
i=0
# Print the map
for doc in documents:
    if(i<5):
        print(doc)
        i+=1

ug7v899j
02tnwd4m
ejv2xln0
2b73a28n
9785vg6d
clinical features mycoplasma pneumoniae infections king abdulaziz university hospital jeddah saudi arabia objective retrospective chart review describes epidemiology clinical features patients mycoplasma pneumoniae infections king abdulaziz university hospital jeddah saudi arabia methods patients positive pneumoniae cultures respiratory specimens january december identified microbiology records charts patients reviewed results patients identified required admission infections infection affected age groups common infants children occurred common fall spring patients comorbidities isolates associated pneumonia upper respiratory tract infections bronchiolitis cough fever malaise common symptoms crepitations wheezes common signs patients pneumonia crepitations bronchial breathing immunocompromised patients likely patients present pneumonia versus p patients pneumonia uneventful recovery recovered following complications died pneumoniae infection

In [39]:
# Create a map to store the last value in each row
last_values_map = {}

# Iterate over the rows of tfidf_matrix
for row in range(tfidf_matrix.shape[0]):
    # Get the last element of each row
    last_col = tfidf_matrix.indices[tfidf_matrix.indptr[row + 1] - 1]
    last_value = tfidf_matrix.data[tfidf_matrix.indptr[row + 1] - 1]

    # Get the key from temp corresponding to the row index
    key = list(temp.keys())[row]

    # Store the last value in the map with the key from temp
    last_values_map[key] = last_value
i=0
# Print the map
for key, value in last_values_map.items():
    if(i<5):
        print(value)
        i+=1

0.05896897882350241
0.05638885015536782
0.03228151221761099
0.08816290036678852
0.06348485484128813


In [40]:
i=0
# Print the map
for key, value in last_values_map.items():
    if(i<5):
        print(f"{key}: {value}")
        i+=1

ug7v899j: 0.05896897882350241
02tnwd4m: 0.05638885015536782
ejv2xln0: 0.03228151221761099
2b73a28n: 0.08816290036678852
9785vg6d: 0.06348485484128813


In [41]:
import json
with open('C:/Users/omer/.ir_datasets/cord19/2020-06-19/last_values_map.json', 'w') as f:
        json.dump(dict(last_values_map), f)
    

In [42]:
import json

# Path to the JSON file
file_path = 'C:/Users/omer/.ir_datasets/cord19/2020-06-19/last_values_map.json'

# Reading the JSON file
with open(file_path, 'r') as f:
    last_values_map = json.load(f)

print(last_values_map)


{'ug7v899j': 0.05896897882350241, '02tnwd4m': 0.05638885015536782, 'ejv2xln0': 0.03228151221761099, '2b73a28n': 0.08816290036678852, '9785vg6d': 0.06348485484128813, 'zjufx4fo': 0.017836424684971614, '5yhe786e': 0.040845003718417046, '8zchiykl': 0.05082374503756129, '8qnrcgnk': 0.03616092167975753, 'jg13scgo': 0.02608450062482154, '5tkvsudh': 0.037002326674181095, '6lvn10f4': 0.028444356791019313, 'tvxpckxo': 0.03186301520722842, 'mcuixluu': 0.021322506358579546, 't35n7bk9': 0.03655959147922902, 'eiqypt0m': 0.04586732455583939, 'sgmk96vr': 0.0164989049687665, 'di0fcy0j': 0.020831112549985237, '4k8f7ou1': 0.018416328417191014, 'wnnsmx60': 0.05443170961455271, 'gdsfkw1b': 0.027339968437959456, 'yba7mdtb': 0.022249442896190012, 'bbvxu8op': 0.036081268148927384, 'e62cfqt7': 0.047858805271077214, '4cvy9u28': 0.014047799883463186, 'zowp10ts': 0.053622184710055844, '5dk231qs': 0.022172875622919926, 'snqdma0s': 0.023570596103062322, '1pq6dkl5': 0.02630053735138296, '754nln40': 0.05009742870799

In [43]:
import json

# Path to the JSON file
file_path = 'C:/Users/omer/.ir_datasets/cord19/2020-06-19/last_values_map.json'

# Reading the JSON file
with open(file_path, 'r') as f:
    last_values_map = json.load(f)

print(last_values_map)


{'ug7v899j': 0.05896897882350241, '02tnwd4m': 0.05638885015536782, 'ejv2xln0': 0.03228151221761099, '2b73a28n': 0.08816290036678852, '9785vg6d': 0.06348485484128813, 'zjufx4fo': 0.017836424684971614, '5yhe786e': 0.040845003718417046, '8zchiykl': 0.05082374503756129, '8qnrcgnk': 0.03616092167975753, 'jg13scgo': 0.02608450062482154, '5tkvsudh': 0.037002326674181095, '6lvn10f4': 0.028444356791019313, 'tvxpckxo': 0.03186301520722842, 'mcuixluu': 0.021322506358579546, 't35n7bk9': 0.03655959147922902, 'eiqypt0m': 0.04586732455583939, 'sgmk96vr': 0.0164989049687665, 'di0fcy0j': 0.020831112549985237, '4k8f7ou1': 0.018416328417191014, 'wnnsmx60': 0.05443170961455271, 'gdsfkw1b': 0.027339968437959456, 'yba7mdtb': 0.022249442896190012, 'bbvxu8op': 0.036081268148927384, 'e62cfqt7': 0.047858805271077214, '4cvy9u28': 0.014047799883463186, 'zowp10ts': 0.053622184710055844, '5dk231qs': 0.022172875622919926, 'snqdma0s': 0.023570596103062322, '1pq6dkl5': 0.02630053735138296, '754nln40': 0.05009742870799

In [44]:
data_title = {}
data_abstract={}
for i, row in ddf.iterrows():
    # Tokenize the title and abstract and remove stop words
    title = row['title']
    abstract = row['abstract']
    
    # Add the tokenized title and abstract to the dictionary
    data_title[str(row['cord_uid'])] = str(title) 
    data_abstract[str(row['cord_uid'])]=str(abstract)

    

In [45]:
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.stem import PorterStemmer, WordNetLemmatizer
def remove_stopwords(text):
    # tokenize the text
    words = nltk.word_tokenize(text)
    
    # remove stop words
    words = [word for word in words if word.lower() not in stopwords.words('english')]
    
    # join the remaining words back into a string
    text_without_stopwords = ' '.join(words)
    
    return text_without_stopwords

Correct Spelling

In [46]:
from textblob import TextBlob

def correct_spelling(query):
    # Create a TextBlob object
    blob = TextBlob(query)

    # Correct the spelling
    corrected_query = str(blob.correct())

    return corrected_query


# ========== ==== Befor Apply Algorithms================

In [73]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

# Assuming you have a list of documents stored in a variable `documents`

# Add more documents as needed]  # Your list of documents here

# Initialize the TfidfVectorizer
vectorizer = TfidfVectorizer()

# Fit the vectorizer on the documents and transform the documents into TF-IDF vectors
tfidf_matrix = vectorizer.fit_transform(documents)

# Now proceed with your existing code
predicted_documents = []
query = input("Enter your query: ")
pureQuery = query

# Apply the defined functions on the input query
query = correct_spelling(query)
print(query)
query = replace_percont_text(query)
query = expand_country_abbreviations(query)
query = expand_date_abbreviations(query)
query = clean_text(query)
query = remove_stopwords(query)
query = lemmatize_text(query)
query = stem_text(query)

print(query)

# Transform the query into a TF-IDF vector
query_vector = vectorizer.transform([query])

# Compute the cosine similarity between the query vector and the documents' TF-IDF vectors
cosine_similarities = cosine_similarity(query_vector, tfidf_matrix)
print(cosine_similarities)

# Get the index of the most similar document
most_similar_document_index = cosine_similarities.argmax()

# Get the similarity score of the most similar document
similarity_score = cosine_similarities[0, most_similar_document_index]
# Get the indices of the top 10 most similar documents
top_indices = cosine_similarities.argsort()[0][-10:][::-1]

# Assuming you have a dictionary `keys` to map indices to document identifiers
# Check if keys[idx] exists in the keys dictionary before accessing it
for idx in top_indices:
    if idx in keys:
        predicted_documents.append(keys[idx])

print(len(predicted_documents))
# Print the most similar document and its similarity score
most_similar_document = documents[most_similar_document_index]

# Get the key (document identifier) of the most similar document
most_similar_document_key = list(temp.keys())[most_similar_document_index]

print("**most_similar_document_key****")
print(most_similar_document_key)


#print("Most similar document:", most_similar_document)
print("Similarity score:", similarity_score)

# Assuming you have a dictionary `data_title` and `data_abstract` to get titles and abstracts of documents
print(data_title[str(most_similar_document_key)])
print(data_abstract[str(most_similar_document_key)])


Enter your query:  coronavirus origin


coronavirus origin
coronaviru origin
[[0. 0.]]
0
**most_similar_document_key****
ug7v899j
Similarity score: 0.0
Clinical features of culture-proven Mycoplasma pneumoniae infections at King Abdulaziz University Hospital, Jeddah, Saudi Arabia
OBJECTIVE: This retrospective chart review describes the epidemiology and clinical features of 40 patients with culture-proven Mycoplasma pneumoniae infections at King Abdulaziz University Hospital, Jeddah, Saudi Arabia. METHODS: Patients with positive M. pneumoniae cultures from respiratory specimens from January 1997 through December 1998 were identified through the Microbiology records. Charts of patients were reviewed. RESULTS: 40 patients were identified, 33 (82.5%) of whom required admission. Most infections (92.5%) were community-acquired. The infection affected all age groups but was most common in infants (32.5%) and pre-school children (22.5%). It occurred year-round but was most common in the fall (35%) and spring (30%). More than three-q

In [48]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

predicted_documents = []
query = input("Enter your query: ")
pureQuery = query
# apply the defined functions on the input query
query = correct_spelling(query)
print(query)
query = replace_percont_text(query)
query = expand_country_abbreviations(query)
query = expand_date_abbreviations(query)
query = clean_text(query)
query = remove_stopwords(query)
query = lemmatize_text(query)
query = stem_text(query)

print(query)
# Transform the query into a TF-IDF vector
query_vector = vectorizer.transform([query])

# Compute the cosine similarity between the query vector and the documents' TF-IDF vectors
cosine_similarities = cosine_similarity(query_vector, tfidf_matrix)
print(cosine_similarities)

# Get the index of the most similar document
most_similar_document_index = cosine_similarities.argmax()

# Get the similarity score of the most similar document
similarity_score = cosine_similarities[0, most_similar_document_index]
# Get the indices of the top 10 most similar documents
top_indices = cosine_similarities.argsort()[0][-10:][::-1]


# Check if keys[idx] exists in the keys dictionary before accessing it
for idx in top_indices:
    if idx in keys:
        predicted_documents.append(keys[idx])

print(len(predicted_documents))
# Print the most similar document and its similarity score
most_similar_document = documents[most_similar_document_index]

# Get the key (document identifier) of the most similar document
most_similar_document_key = list(temp.keys())[most_similar_document_index]

print("**most_similar_document_key****")
print(most_similar_document_key)

#print("Most similar document:", most_similar_document)
print("Similarity score:", similarity_score)


print(data_title[str(most_similar_document_key)])
print(data_abstract[str(most_similar_document_key)])


Enter your query:  COVID-19 cytokine storm


COVID-19 cytokine storm
covid 19 cytokin storm
[[0. 0.]]
0
**most_similar_document_key****
ug7v899j
Similarity score: 0.0
Clinical features of culture-proven Mycoplasma pneumoniae infections at King Abdulaziz University Hospital, Jeddah, Saudi Arabia
OBJECTIVE: This retrospective chart review describes the epidemiology and clinical features of 40 patients with culture-proven Mycoplasma pneumoniae infections at King Abdulaziz University Hospital, Jeddah, Saudi Arabia. METHODS: Patients with positive M. pneumoniae cultures from respiratory specimens from January 1997 through December 1998 were identified through the Microbiology records. Charts of patients were reviewed. RESULTS: 40 patients were identified, 33 (82.5%) of whom required admission. Most infections (92.5%) were community-acquired. The infection affected all age groups but was most common in infants (32.5%) and pre-school children (22.5%). It occurred year-round but was most common in the fall (35%) and spring (30%). More th

# ============ Start Clustring ================

In [80]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans

# Clustering
num_clusters = 5 # Set the number of clusters as desired
kmeans = KMeans(n_clusters=num_clusters, random_state=42)
cluster_labels = kmeans.fit_predict(tfidf_matrix)



In [81]:
# Create a DataFrame to store the cluster labels
cluster_data = pd.DataFrame({'Cluster Label': cluster_labels})

# Specify the file path for storing the CSV file
file_path = 'C:/Users/omer/.ir_datasets/cord19/2020-06-19/files/cluster_labels.csv'

# Save the cluster labels to the specified file path
cluster_data.to_csv(file_path, index=False)


In [78]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans
from sklearn.decomposition import LatentDirichletAllocation


predicted_documents = []

# User query
query = input("Enter your query: ")
pureQuery = query
# Preprocess the query
# Apply the defined preprocessing functions on the input query
query = correct_spelling(query)
query = replace_percont_text(query)
query = expand_country_abbreviations(query)
query = expand_date_abbreviations(query)
query = clean_text(query)
query = remove_stopwords(query)
query = lemmatize_text(query)
query = stem_text(query)

# Transform the query into a TF-IDF vector
query_vector = vectorizer.transform([query])

# Cosine Similarity
cosine_similarities = cosine_similarity(query_vector, tfidf_matrix)
most_similar_document_index = cosine_similarities[0].argmax()
similarity_score = cosine_similarities[0, most_similar_document_index]

# Cluster Algorithm
query_cluster = cluster_labels[most_similar_document_index]
cluster_indices = [i for i, label in enumerate(cluster_labels) if label == query_cluster]
print("The result of Cluster Algorithm search: ", len(cluster_indices))
cluster_similarities = cosine_similarities[0, cluster_indices]
sorted_indices = np.array(cluster_indices)[np.argsort(cluster_similarities)[::-1]]

# Update predicted_documents with the correct key indexing
predicted_documents += [keys[idx] for idx in sorted_indices if idx in keys]

top_indices = sorted_indices[:10]

most_similar_document_key = list(temp.keys())[most_similar_document_index]

print("**most_similar_document_key****")
print(most_similar_document_key)

#print("Most similar document:", most_similar_document)
print("Similarity score:", similarity_score)


print(data_title[str(most_similar_document_key)])
print(data_abstract[str(most_similar_document_key)])


Enter your query:  coronavirus origin


ValueError: Incompatible dimension for X and Y matrices: X.shape[1] == 3 while Y.shape[1] == 151786

# ============ End Clustring ================

# ============ Start Topic ================

In [82]:
from sklearn.decomposition import LatentDirichletAllocation
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans


# Topic Detection
num_topics = 3  # Set the number of topics as desired
lda = LatentDirichletAllocation(n_components=num_topics, random_state=42)
topic_weights = lda.fit_transform(tfidf_matrix)


============= read and write file topic =============

In [83]:
import pandas as pd
from sklearn.decomposition import LatentDirichletAllocation

# Create a DataFrame to store the topic weights
topic_data = pd.DataFrame(topic_weights)

# Specify the file path for storing the CSV file
file_path = 'C:/Users/omer/.ir_datasets/cord19/2020-06-19/files/topic_weights.csv'

# Save the topic weights to the specified file path
topic_data.to_csv(file_path, index=False)


In [55]:
import pandas as pd

# Specify the file path of the CSV file containing the topic weights
file_path = 'C:/Users/omer/.ir_datasets/cord19/2020-06-19/files/topic_weights.csv'

# Read the topic weights from the CSV file
topic_data = pd.read_csv(file_path)

# Access the topic weights as a NumPy array
topic_weights = topic_data.to_numpy()


=========== applay topic ================

In [56]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans
from sklearn.decomposition import LatentDirichletAllocation


predicted_documents = []

# User query
query = input("Enter your query: ")
pureQuery = query
# Preprocess the query
# Apply the defined preprocessing functions on the input query
query = correct_spelling(query)
query = replace_percont_text(query)
query = expand_country_abbreviations(query)
query = expand_date_abbreviations(query)
query = clean_text(query)
query = remove_stopwords(query)
query = lemmatize_text(query)
query = stem_text(query)

# Transform the query into a TF-IDF vector
query_vector = vectorizer.transform([query])

# Cosine Similarity
cosine_similarities = cosine_similarity(query_vector, tfidf_matrix)
most_similar_document_index = cosine_similarities.argmax()
similarity_score = cosine_similarities[0, most_similar_document_index]

# Topic Algorithm
most_similar_topic_weights = topic_weights[most_similar_document_index]
best_topic_index = most_similar_topic_weights.argmax()
documents_in_best_topic = [i for i, weight in enumerate(topic_weights[:, best_topic_index]) if weight > 0]
topic_similarities = cosine_similarities[0, documents_in_best_topic]
sorted_indices_within_topic = np.array(documents_in_best_topic)[np.argsort(topic_similarities)[::-1]]

top_indices_within_topic = sorted_indices_within_topic[:10]
print("The result of Topic Algorithm search : ",len(top_indices_within_topic))
predicted_documents += [keys[idx] for idx in sorted_indices]
# Print the most similar documents within the best topic and their similarity scores
for idx in top_indices_within_topic:
    most_similar_document_key = list(temp.keys())[idx]
    print("Title:", data_title[str(most_similar_document_key)])

# Print the best-weighted topic and its weight
print("Best-weighted topic:")
print("Topic", best_topic_index, "- Weight:", most_similar_topic_weights[best_topic_index])


Enter your query:  COVID-19 cytokine storm


The result of Topic Algorithm search :  2
Title: Nitric oxide: a pro-inflammatory mediator in lung disease?
Title: Clinical features of culture-proven Mycoplasma pneumoniae infections at King Abdulaziz University Hospital, Jeddah, Saudi Arabia
Best-weighted topic:
Topic 1 - Weight: 0.7426137913911158


# ============ End Topic ================

# Start Evaluation Precission and Recall 

# ================== testing  ===============

In [84]:
import xml.etree.ElementTree as ET

def get_query_indices(query):
    # Parse the XML fileC:
    tree = ET.parse('C:/Users/omer/.ir_datasets/cord19/trec-covid/round4/queries.xml')
    root = tree.getroot()

    query_number = -1
    
    # Iterate over topic elements
    for index, topic in enumerate(root.findall('topic'), 1):
        topic_number = int(topic.get('number'))
        topic_query = topic.find('query').text
        
        if str(topic_query) == str(query):
            query_number = topic_number
    return query_number

print(pureQuery)

data = []
query_number = get_query_indices(pureQuery)
print(query_number)
i = 0

with open('C:/Users/omer/.ir_datasets/cord19/trec-covid/round4/qrels', 'r') as file:
    for i, line in enumerate(file, 1):
        query_parts = line.strip().split()
        if int(query_parts[0]) == int(query_number):
            data.append(i)

print(len(data))
print(data[0])
print(data[-1])

coronavirus origin
1
257
1
257


In [87]:
# Read the relevance judgments from the file
relevant_documents = []  # List of relevant document IDs for the query

def precision_at_k(actual, predicted, k):
    if len(predicted) > k:
        predicted = predicted[:k]
    tp = len(set(actual) & set(predicted))
    print(tp)
    precision = tp / len(predicted)
    return precision

with open(r'C:/Users/omer/.ir_datasets/cord19/trec-covid/round4/qrels', 'r') as file:
    i=0   
    for line in file:
        query_id, iteration, doc_id, relevance = line.split()
        if i>=data[0] and i <= data[-1]:
            relevant_documents.append(doc_id)     
        i+=1
        
print('********************')
print(relevant_documents[:10])
print(predicted_documents)
print(len(predicted_documents))
# Calculate Precision@10, Precision, and Recall
precision_10 = precision_at_k(relevant_documents,predicted_documents, 10)
precision = precision_at_k(relevant_documents, predicted_documents, len(predicted_documents))
recall = len(set(relevant_documents) & set(predicted_documents)) / len(relevant_documents)



# Calculate Mean Average Precision (MAP)
average_precision = 0
relevant_count = 0
for i, doc in enumerate(predicted_documents):
    if doc in relevant_documents:
        relevant_count += 1
        precision_at_i = relevant_count / (i + 1)
        average_precision += precision_at_i
if relevant_count > 0:
    average_precision /= relevant_count



# Calculate Mean Reciprocal Rank (MRR)
reciprocal_rank = 0
for i, doc in enumerate(predicted_documents):
    if doc in relevant_documents:
        reciprocal_rank = 1 / (i + 1)
        break
# Print the metrics
print("Precision@10:", precision_10)
print("Precision:", precision)
print("Recall:", recall)
print("MAP:", average_precision)
print("MRR:", reciprocal_rank)

********************
['021q9884', '047xpt2c', '0chuwvg6', '0iq9s94n', '0m5mc320', '0v5wo0ty', '105q161g', '10ecm4wi', '1c47w4q5', '1ldynibm']
[]
0
0


ZeroDivisionError: division by zero

# =================== end testing  =============

In [59]:
data = []

with open(r'C:\Users\omer\.ir_datasets\cord19\trec-covid\round4\qrels', 'r') as file:
    for line in file:
        query_parts = line.strip().split('\t')
        try:
            if int(query_parts[0]) == int(query_number):
                data.append(int(query_parts[2]))
        except ValueError:
            pass  # Skip non-integer lines

print(data)  # Print data for debugging

if data:
    print(data[0])
    print(data[-1])
else:
    print("No data found.")



[]
No data found.


# ========================= test above ====================

In [60]:
def precision_at_k(actual, predicted, k):
    if len(predicted) > k:
        predicted = predicted[:k]
    tp = len(set(actual) & set(predicted))
    print(tp)
    print(len(predicted))
    precision = tp / len(predicted)
    return precision



keyQuery=0
first=0
last=0


for key,value in query_map_keys.items():
    if(value==pureQuery):
        keyQuery=key

        
# Read the relevance judgments from the file
relevant_documents = []  # List of relevant document IDs for the query

with open(r'C:\Users\omer\.ir_datasets\cord19\trec-covid\round4\qrels', 'r') as file:
    i=0   
    for line in file:
        query_id, iteration, doc_id, relevance = line.split()
        if(i>=first and i <= last):
            relevant_documents.append(doc_id)
            i+=1
        


# Calculate Precision@10, Precision, and Recall
print("**************************")
print(len(predicted_documents))
print(len(relevant_documents))
precision_10 = precision_at_k(relevant_documents,predicted_documents, 10)
precision = precision_at_k(relevant_documents, predicted_documents, len(predicted_documents))
recall = len(set(relevant_documents) & set(predicted_documents)) / len(relevant_documents)



# Calculate Mean Average Precision (MAP)
average_precision = 0
relevant_count = 0
for i, doc in enumerate(predicted_documents):
    if doc in relevant_documents:
        relevant_count += 1
        precision_at_i = relevant_count / (i + 1)
        average_precision += precision_at_i

if relevant_count > 0:
    average_precision /= relevant_count

# Calculate Mean Reciprocal Rank (MRR)
reciprocal_rank = 0
for i, doc in enumerate(predicted_documents):
    if doc in relevant_documents:
        reciprocal_rank = 1 / (i + 1)
        break

# Print the metrics
print("Precision@10:", precision_10)
print("Precision:", precision)
print("Recall:", recall)
print("MAP:", average_precision)

print("MRR:", reciprocal_rank)


NameError: name 'query_map_keys' is not defined

In [61]:
query_map = {}

with open(r'C:\Users\omer\.ir_datasets\cord19\trec-covid\round4\qrels', 'r') as file:
    lines = file.readlines()
    for line_number, line in enumerate(lines, 1):
        query_parts = line.strip().split()
        query_number = int(query_parts[0])
        query_key = query_parts[2]
        if query_number not in query_map:
            query_map[query_number] = {'firstElement': line_number, 'lastElement': line_number}
        else:
            query_map[query_number]['lastElement'] = line_number

# Print the map
for query_number, elements in query_map.items():
    print(f"Query Number: {query_number}")
    print(f"First Element: line number {elements['firstElement']}")
    print(f"Last Element: line number {elements['lastElement']}")
    print()


Query Number: 1
First Element: line number 1
Last Element: line number 257

Query Number: 2
First Element: line number 258
Last Element: line number 422

Query Number: 3
First Element: line number 423
Last Element: line number 742

Query Number: 4
First Element: line number 743
Last Element: line number 1090

Query Number: 5
First Element: line number 1091
Last Element: line number 1401

Query Number: 6
First Element: line number 1402
Last Element: line number 1673

Query Number: 7
First Element: line number 1674
Last Element: line number 1863

Query Number: 8
First Element: line number 1864
Last Element: line number 2175

Query Number: 9
First Element: line number 2176
Last Element: line number 2435

Query Number: 10
First Element: line number 2436
Last Element: line number 2611

Query Number: 11
First Element: line number 2612
Last Element: line number 2928

Query Number: 12
First Element: line number 2929
Last Element: line number 3191

Query Number: 13
First Element: line number 31

In [63]:
import xml.etree.ElementTree as ET

# XML data
import json


# Specify the path to the XML file

xml_file_path = 'C:/Users/omer/.ir_datasets/cord19/trec-covid/round4/queries.xml'

# Parse the XML file
tree = ET.parse(xml_file_path)
root = tree.getroot()

# Create a map to store the queries
query_map_keys = {}

# Iterate over topic elements
for topic in root.findall('topic'):
    number = topic.get('number')
    query = topic.find('query').text
    query_map_keys[query] = number

print(query_map_keys['coronavirus origin'])
# Print the query map
for number, query in query_map_keys.items():
    print(f'Topic {number}: {query}')

1
Topic coronavirus origin: 1
Topic coronavirus response to weather changes: 2
Topic coronavirus immunity: 3
Topic how do people die from the coronavirus: 4
Topic animal models of COVID-19: 5
Topic coronavirus test rapid testing: 6
Topic serological tests for coronavirus: 7
Topic coronavirus under reporting: 8
Topic coronavirus in Canada: 9
Topic coronavirus social distancing impact: 10
Topic coronavirus hospital rationing: 11
Topic coronavirus quarantine: 12
Topic how does coronavirus spread: 13
Topic coronavirus super spreaders: 14
Topic coronavirus outside body: 15
Topic how long does coronavirus survive on surfaces: 16
Topic coronavirus clinical trials: 17
Topic masks prevent coronavirus: 18
Topic what alcohol sanitizer kills coronavirus: 19
Topic coronavirus and ACE inhibitors: 20
Topic coronavirus mortality: 21
Topic coronavirus heart impacts: 22
Topic coronavirus hypertension: 23
Topic coronavirus diabetes: 24
Topic coronavirus biomarkers: 25
Topic coronavirus early symptoms: 26

# End Evaluation Precission and Recall 